# rt-me-fMRI - Reproduce Figures 2

---

## Pipeline and descriptions to reproduce figures and tables for rt-me-fMRI methods article

Sections:

- [Figure 1: Multi-echo decay](#fig1)
- [Figure 2: Analysis pipeline](#fig2)
- [Figure 3: Slice montage of signal decay](#fig3)
- [Figure 4: Slice montage of intensity and tSNR](#fig4)
- [Figure 5: Time series analysis and comparison](#fig5)
- [Figure 6: Group-level statistical maps](#fig6)
- [Figure 7: Axial slice montages of single and multi-echo time series tSNR](#fig7)
- [Figure 8: Mean grey matter tSNR distributions over all subjects and tasks](#fig8)
- [Table: All QC metrics](#table)

<div id="fig1"></div>

# Figure 1: Multi-echo decay

Created with [BioRender](https://biorender.com/)

<img src="figures/methods_article/fig1.png" alt="fig1" style="width: 40%;"/>

<div id="fig2"></div>

# Figure 2: Analysis pipeline

Created with [BioRender](https://biorender.com/)

<img src="figures/methods_article/fig2.png" alt="fig2" style="width: 66%;"/>

<div id="fig3"></div>

# Figure 3: Slice montage of signal decay

Created with [BioRender](https://biorender.com/)

<img src="figures/methods_article/fig3.png" alt="fig3" style="width: 70%;"/>

<div id="fig4"></div>

# Figure 4: Slice montage of intensity and tSNR

Created with [BioRender](https://biorender.com/)

<img src="figures/methods_article/fig4.png" alt="fig4" style="width: 70%;"/>

# RF1-RF3: Image intensity and tSNR to show decay, dropout and recovery

This includes montages of:

- Single volumes of echos to show decay (RF1)
- Image intensity volumes from all six timeseries to show dropout and signal recovery (RF2)
- tSNR volumes from of all six timeseries to show dropout and signal recovery (RF3)

All of these are generated by the Matlab script `rtme_reproduce_methodsFigures`.

This requires access to the preprocessed data of the rt-me-fMRI dataset.

## 1. Imports

In [1]:
%load_ext autoreload
%autoreload 2
import sys
sys.path.append("python")
from jupyter_dash import JupyterDash
import dash
import dash_core_components as dcc
import dash_html_components as html
import dash_bootstrap_components as dbc
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import shutil
import glob
import os
import math
from IPython.display import display, set_matplotlib_formats
import nibabel as nib
from nilearn import plotting
from nilearn.image import load_img
from dash.dependencies import Input, Output
from dash.exceptions import PreventUpdate
from plotly.colors import sequential, n_colors
import plotly.graph_objs as go
from bids import BIDSLayout
from nilearn.image.image import mean_img
import utilities as util

/Users/jheunis/miniconda3/envs/rtme-fmri/lib/python3.7/site-packages/sklearn/externals/joblib/__init__.py:15: DeprecationWarning: sklearn.externals.joblib is deprecated in 0.21 and will be removed in 0.23. Please import this functionality directly from joblib, which can be installed with: pip install joblib. If this warning is raised when loading pickled models, you may need to re-serialize those models with scikit-learn 0.21+.
  warnings.warn(msg, category=DeprecationWarning)


# RF4: tSNR distribution in grey matter for all time series, sub-001_task-rest_run-2

In [10]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
sub = 'sub-001'
task = 'rest_run-2'
ts_names = ['t2starFIT', 'combinedMEt2starFIT', 'combinedMEte', 'combinedMEt2star', 'combinedMEtsnr', 'echo-2']
ts_names_disp = ['T2*FIT', 'T2*FIT-combined', 'TE-combined', 'T2*-combined', 'tSNR-combined', 'Echo 2']

layout = go.Layout(
    yaxis = dict(title = 'Time series'),
    xaxis=dict(title='Temporal signal-to-noise ratio in Gray Matter (a.u.)', range=[-20, 300]),
    height = 600,
    margin={
          't': 10,
        })
# Colormaps from https://colorbrewer2.org/#type=qualitative&scheme=Dark2&n=6
colors = [['#a6cee3', '#1f78b4', '#b2df8a', '#33a02c', '#fb9a99', '#e31a1c'],
           ['#e41a1c', '#377eb8', '#4daf4a', '#984ea3', '#ff7f00', '#ffff33'],
           ['#8dd3c7', '#ffffb3', '#bebada', '#fb8072', '#80b1d3', '#fdb462'],
           ['#1b9e77', '#d95f02', '#7570b3', '#e7298a', '#66a61e', '#e6ab02']] 
fig_tsnr_persub = go.Figure(layout=layout)

data = []
for x, ts in enumerate(ts_names):
    if x == 5:
        GMtsnr_tsv = os.path.join(data_dir, 'multiecho', sub+'_task-'+task+'_echo-2_desc-rapreproc_GMtsnr.tsv')
    else:
        GMtsnr_tsv = os.path.join(data_dir, 'multiecho', sub+'_task-'+task+'_desc-' + ts + '_GMtsnr.tsv')

    df_GMtsnr = pd.read_csv(GMtsnr_tsv, sep='\t').dropna()
    new_dat = df_GMtsnr['tsnr'].to_numpy()
    if x == 0:
        new_dat[new_dat < 0] = math.nan
        new_dat[new_dat > 500] = math.nan
    
    data.append(new_dat)
    fig_tsnr_persub.add_trace(go.Violin(x=data[x], line_color=colors[3][5-x], name=ts_names_disp[x], points=False))

fig_tsnr_persub.update_traces(orientation='h', side='positive', width=2, box_visible=True, meanline_visible=True)
fig_tsnr_persub.update_layout(
    xaxis_showgrid=True, 
    yaxis_showgrid=True, 
    xaxis_zeroline=False, 
    legend={'traceorder':'reversed'},
    font=dict(
        size=16,
    )
)

for i, ts in enumerate(ts_names):
    
    mean = np.nanmean(data[i])
    fig_tsnr_persub.add_annotation(
        x=mean,
        y=i,
        xref="x",
        yref="y",
        text=f"Mean={mean:.2f}",
        showarrow=True,
        font=dict(
            family="Courier New, monospace",
            size=15,
            color="#ffffff"
            ),
        align="center",
        arrowhead=2,
        arrowsize=0.7,
        arrowwidth=2,
        arrowcolor="#ffffff",
        ax=70,
        ay=-40,
        bordercolor="#ffffff",
        borderwidth=1.75,
        borderpad=4,
        bgcolor=colors[3][5-i],
        opacity=0.8
        )
fig_tsnr_persub.show()

## 4. RF5: Mean grey matter tSNR distributions over all subjects and all runs

In [7]:
layout = go.Layout(
        yaxis = dict(title = 'Mean tSNR in gray matter (a.u.)', range=[0, 250]),
        xaxis = dict(title='Time series'),
        margin = {
              't': 10,
            },
        font=dict(size=16)
)
tsnr_regions = ['whole brain', 'lmotor', 'bamygdala']
fig_tsnr_mean = [None, None, None]
tsnr_runs = ['all runs', 'fingerTapping', 'emotionProcessing', 'rest_run-2', 'fingerTappingImagined', 'emotionProcessingImagined']
tsnr_run = tsnr_runs[0]
for i, region in enumerate(tsnr_regions):
    fig_tsnr_mean[i] = util.reset_tsnr_summary(go.Figure(layout=layout), data_dir, region, tsnr_run)

In [8]:
# RF5-A
fig_tsnr_mean[0]

In [11]:
# RF5-B
fig_tsnr_mean[1]

In [12]:
# RF5-C
fig_tsnr_mean[2]

## PSC

# RF6

In [15]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
        yaxis = dict(title = 'Precentage signal change', range=[0, 3.25]), # 
        xaxis = dict(title='Time series'),
        margin = {
              't': 10,
            })

fig_psc_summary = [None, None, None, None]
tasks = ['fingerTapping', 'fingerTappingImagined', 'emotionProcessing', 'emotionProcessingImagined']
summary_opt = 'mean'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
cluster_opt = cluster_opts[1]
for i, task in enumerate(tasks):
    fig_psc_summary[i] = util.reset_psc_summary_img(go.Figure(layout=layout), data_dir, task, summary_opt, cluster_opt)

In [16]:
# RF6A
fig_psc_summary[0]

In [17]:
# RF6B
fig_psc_summary[1]

In [18]:
# RF6C
fig_psc_summary[2]

In [19]:
# RF6D
fig_psc_summary[3]

In [20]:
#RF7A-H: not sure if this will eventually be plotted. Leaving out for now.

# T-values - RF8ABC

In [21]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    yaxis = dict(title = 'T-values (a.u.)', range=[0, 12]),
    xaxis = dict(title='Time series'),
    margin = {
          't': 10,
        })
fig_tvals_summary = [None, None, None, None]
tasks = ['fingerTapping', 'fingerTappingImagined', 'emotionProcessing', 'emotionProcessingImagined']
summary_opt = 'mean'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
cluster = cluster_opts[1]
for i, task in enumerate(tasks):
    fig_tvals_summary[i] = util.reset_tval_summary_img(go.Figure(layout=layout), data_dir, task, summary_opt, cluster_opt)


In [22]:
# RF8A
fig_tvals_summary[0]

In [23]:
# RF8B
fig_tvals_summary[1]

In [24]:
# RF8C
fig_tvals_summary[2]

In [25]:
# RF8C
fig_tvals_summary[3]

# Offline tPCS and functional contrast - RF9ABC

In [26]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    yaxis = dict(title = 'Percentage signal change', range=[-2, 2.2]),
    xaxis=dict(title='Time (functional volumes)'),
    margin={
          't': 10,
        })
fig_psc_timeseries = [None, None, None]
sub = 'sub-001'
task = 'fingerTapping'
cluster_opts = ['FWE', 'fweOR', 'anatROI']
for i, cluster_opt in enumerate(cluster_opts):
    fig_psc_timeseries[i] = util.reset_psc_timeseries_img(go.Figure(layout=layout), data_dir, sub, task, cluster_opt)


In [27]:
fig_psc_timeseries[0]

In [28]:
fig_psc_timeseries[1]

In [29]:
fig_psc_timeseries[2]

In [32]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
        xaxis = dict(title = 'Time series'),
        yaxis = dict(title='Functional contrast (offline PSC)', range=[-0.5, 2]),
        margin={
              't': 10,
            })

fig_cnr_offline = [None, None, None, None, None, None]
tasks = ['fingerTapping', 'emotionProcessing']
cnr_opt = 'cnr'
# cluster_opts = ['FWE', 'noFWE', 'anatROI', 'fweAND', 'fweOR']
cluster_opts = ['fweOR', 'anatROI']
i = 0
for t, task in enumerate(tasks):
    for c, cluster_opt in enumerate(cluster_opts):
        fig_cnr_offline[i] = util.reset_psc_cnr_img(go.Figure(layout=layout), data_dir, cnr_opt, task, cluster_opt)
        i += 1

In [33]:
fig_cnr_offline[0]

In [34]:
fig_cnr_offline[1]

In [35]:
fig_cnr_offline[2]

In [36]:
fig_cnr_offline[3]

# Real-time contrast and tCNR

In [37]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    xaxis = dict(title = 'Time series'),
    yaxis = dict(title='Functional contrast (real-time PSC)', range=[-0.5, 3]),
    margin={
          't': 10,
        })
fig_realtime_summary = [None, None, None, None, None, None]

tasks = ['fingerTapping', 'emotionProcessing']
cnr_opt = 'cnr'
psc_types = ['glm', 'offline', 'cumulative', 'cumulativebas', 'previousbas']
psc_opt = psc_types[3]
clusters = [None, None]
clusters[0] = ['OR', 'rleftMotor']
clusters[1] = ['OR', 'rbilateralAmygdala']
i = 0
for t, task in enumerate(tasks):
    for c, cluster in enumerate(clusters[t]):
        fig_realtime_summary[i] = util.reset_realtime_summary_img(go.Figure(layout=layout), data_dir, cnr_opt, task, cluster, psc_opt)
        i+=1

In [38]:
fig_realtime_summary[0]

In [39]:
fig_realtime_summary[1]

In [40]:
fig_realtime_summary[2]

In [41]:
fig_realtime_summary[3]

In [42]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
    xaxis = dict(title = 'Time series'),
    yaxis = dict(title='Temporal contrast-to-noise ratio', range=[-0.5, 2]),
    margin={
          't': 10,
        })
fig_realtime_tcnr = [None, None]

tasks = ['fingerTapping', 'emotionProcessing']
cnr_opt = 'tcnr'
psc_types = ['glm', 'offline', 'cumulative', 'cumulativebas', 'previousbas']
psc_opt = psc_types[3]
cluster = 'OR'
for t, task in enumerate(tasks):
    fig_realtime_tcnr[t] = util.reset_realtime_summary_img(go.Figure(layout=layout), data_dir, cnr_opt, task, cluster, psc_opt)

In [43]:
fig_realtime_tcnr[0]

In [44]:
fig_realtime_tcnr[1]

## Real-time time series plots

In [46]:
data_dir = '/Users/jheunis/Documents/Websites/rt-me-fmri-data-v2'
layout = go.Layout(
        yaxis = dict(title = 'Percentage signal change', range=[-2.5, 2.5]),
        xaxis=dict(title='Time (functional volumes)'),
        margin={
              't': 10,
            })

fig_realtime_series = [None, None, None, None, None, None]
sub = 'sub-001'
tasks = ['fingerTapping', 'emotionProcessing']
cluster_opts = ['FWE', 'fweOR', 'anatROI']
psc_types = ['glm', 'offline', 'cumulative', 'cumulativebas', 'previousbas']
psc_opt = psc_types[3]
clusters = [None, None]
clusters[0] = ['OR', 'rleftMotor']
clusters[1] = ['OR', 'rbilateralAmygdala']
j = 0
for t, task in enumerate(tasks):
    for i, cluster_opt in enumerate(clusters[t]):
        fig_realtime_series[j] = util.reset_realtime_series_img(go.Figure(layout=layout), data_dir, sub, task, cluster_opt, psc_opt)
        j+=1


In [47]:
fig_realtime_series[0]

In [48]:
fig_realtime_series[1]

In [49]:
fig_realtime_series[2]

In [50]:
fig_realtime_series[3]

In [51]:
fig_realtime_series[4]

In [52]:
fig_realtime_series[5]